# Generating a Metallica Song using an LSTM

![title](data/Metallica_Logo.jpg)

In [1]:


from __future__ import print_function
import IPython
import sys
from music21 import *
import numpy as np
from grammar import *
from qa import *
from preprocess import * 
from music_utils import *
from data_utils import *
from keras.models import load_model, Model
from keras.layers import Dense, Activation, Dropout, Input, LSTM, Reshape, Lambda, RepeatVector
from keras.initializers import glorot_uniform
from keras.utils import to_categorical
from keras.optimizers import Adam
from keras import backend as K
import warnings

warnings.filterwarnings('ignore')


/home/hvyd/anaconda3/lib/python3.5/site-packages/h5py/__init__.py:36: FutureWarning: Conversion of the second argument of issubdtype from `float` to `np.floating` is deprecated. In future, it will be treated as `np.float64 == np.dtype(float).type`.
  from ._conv import register_converters as _register_converters
Using TensorFlow backend.


In [2]:
IPython.display.Audio('./data/metallica.mp3')

In [3]:

X, Y, n_values, indices_values = load_music_utils()
print('shape of X:', X.shape)
print('number of training examples:', X.shape[0])
print('Tx (length of sequence):', X.shape[1])
print('total # of unique values:', n_values)
print('Shape of Y:', Y.shape)

shape of X: (60, 30, 78)
number of training examples: 60
Tx (length of sequence): 30
total # of unique values: 78
Shape of Y: (30, 60, 78)


In [4]:
n_a = 64 

In [5]:
reshapor = Reshape((1, 78))                        
LSTM_cell = LSTM(n_a, return_state = True)         
densor = Dense(n_values, activation='softmax')     


In [6]:
def djmodel(Tx, n_a, n_values):
 
    X = Input(shape=(Tx, n_values))
    a0 = Input(shape=(n_a,), name='a0')
    c0 = Input(shape=(n_a,), name='c0')
    a = a0
    c = c0

   
    outputs = []

    
    for t in range(Tx):

       
        x = Lambda(lambda x: X[:,t,:])(X)
        
        x = reshapor(x)
        
        a, _, c = LSTM_cell(x, initial_state=[a, c])
       
        out = densor(a)
      
        outputs.append(out)

   
    model = Model([X, a0, c0], outputs)


    return model




In [7]:
model = djmodel(Tx = 30 , n_a = 64, n_values = 78)


In [8]:
opt = Adam(lr=0.01, beta_1=0.9, beta_2=0.999, decay=0.01)

model.compile(optimizer=opt, loss='categorical_crossentropy', metrics=['accuracy'])


In [9]:
m = 60
a0 = np.zeros((m, n_a))
c0 = np.zeros((m, n_a))

In [10]:
model.fit([X, a0, c0], list(Y), epochs=100)

Epoch 1/100
60/60 [==============================] - 24s 408ms/step - loss: 125.8610 - dense_1_loss: 0.0000e+00 - dense_1_acc: 0.0167 - dense_1_acc_1: 0.1000 - dense_1_acc_2: 0.1333 - dense_1_acc_3: 0.0667 - dense_1_acc_4: 0.0333 - dense_1_acc_5: 0.1000 - dense_1_acc_6: 0.1167 - dense_1_acc_7: 0.1000 - dense_1_acc_8: 0.0500 - dense_1_acc_9: 0.0500 - dense_1_acc_10: 0.0667 - dense_1_acc_11: 0.0833 - dense_1_acc_12: 0.0833 - dense_1_acc_13: 0.0167 - dense_1_acc_14: 0.0667 - dense_1_acc_15: 0.0167 - dense_1_acc_16: 0.0500 - dense_1_acc_17: 0.0667 - dense_1_acc_18: 0.0667 - dense_1_acc_19: 0.0167 - dense_1_acc_20: 0.0833 - dense_1_acc_21: 0.0667 - dense_1_acc_22: 0.1000 - dense_1_acc_23: 0.0333 - dense_1_acc_24: 0.0333 - dense_1_acc_25: 0.0500 - dense_1_acc_26: 0.0667 - dense_1_acc_27: 0.0500 - dense_1_acc_28: 0.0667 - dense_1_acc_29: 0.0000e+00                                                              
Epoch 2/100
60/60 [==============================] - 0s 2ms/step - loss: 122.4404 - 

60/60 [==============================] - 0s 2ms/step - loss: 57.5372 - dense_1_loss: 0.0000e+00 - dense_1_acc: 0.0667 - dense_1_acc_1: 0.2333 - dense_1_acc_2: 0.3833 - dense_1_acc_3: 0.2500 - dense_1_acc_4: 0.4333 - dense_1_acc_5: 0.4000 - dense_1_acc_6: 0.4833 - dense_1_acc_7: 0.5333 - dense_1_acc_8: 0.5500 - dense_1_acc_9: 0.3833 - dense_1_acc_10: 0.5000 - dense_1_acc_11: 0.4667 - dense_1_acc_12: 0.7000 - dense_1_acc_13: 0.5833 - dense_1_acc_14: 0.3833 - dense_1_acc_15: 0.4000 - dense_1_acc_16: 0.5500 - dense_1_acc_17: 0.4667 - dense_1_acc_18: 0.6000 - dense_1_acc_19: 0.6000 - dense_1_acc_20: 0.5000 - dense_1_acc_21: 0.5000 - dense_1_acc_22: 0.5667 - dense_1_acc_23: 0.4667 - dense_1_acc_24: 0.4333 - dense_1_acc_25: 0.6000 - dense_1_acc_26: 0.5667 - dense_1_acc_27: 0.5833 - dense_1_acc_28: 0.6000 - dense_1_acc_29: 0.0000e+00
Epoch 20/100
60/60 [==============================] - 0s 2ms/step - loss: 54.3537 - dense_1_loss: 0.0000e+00 - dense_1_acc: 0.0667 - dense_1_acc_1: 0.2333 - dense

60/60 [==============================] - 0s 2ms/step - loss: 19.1033 - dense_1_loss: 0.0000e+00 - dense_1_acc: 0.0667 - dense_1_acc_1: 0.3500 - dense_1_acc_2: 0.7333 - dense_1_acc_3: 0.8167 - dense_1_acc_4: 0.8500 - dense_1_acc_5: 0.9833 - dense_1_acc_6: 0.9833 - dense_1_acc_7: 0.9833 - dense_1_acc_8: 0.9833 - dense_1_acc_9: 1.0000 - dense_1_acc_10: 1.0000 - dense_1_acc_11: 0.9667 - dense_1_acc_12: 1.0000 - dense_1_acc_13: 1.0000 - dense_1_acc_14: 1.0000 - dense_1_acc_15: 1.0000 - dense_1_acc_16: 1.0000 - dense_1_acc_17: 1.0000 - dense_1_acc_18: 0.9833 - dense_1_acc_19: 1.0000 - dense_1_acc_20: 1.0000 - dense_1_acc_21: 1.0000 - dense_1_acc_22: 1.0000 - dense_1_acc_23: 1.0000 - dense_1_acc_24: 1.0000 - dense_1_acc_25: 0.9833 - dense_1_acc_26: 1.0000 - dense_1_acc_27: 0.9833 - dense_1_acc_28: 0.9667 - dense_1_acc_29: 0.0167
Epoch 38/100
60/60 [==============================] - 0s 2ms/step - loss: 18.0339 - dense_1_loss: 0.0000e+00 - dense_1_acc: 0.0667 - dense_1_acc_1: 0.3500 - dense_1_a

60/60 [==============================] - 0s 2ms/step - loss: 9.3244 - dense_1_loss: 0.0000e+00 - dense_1_acc: 0.0667 - dense_1_acc_1: 0.5000 - dense_1_acc_2: 0.9000 - dense_1_acc_3: 0.9667 - dense_1_acc_4: 0.9833 - dense_1_acc_5: 1.0000 - dense_1_acc_6: 1.0000 - dense_1_acc_7: 1.0000 - dense_1_acc_8: 1.0000 - dense_1_acc_9: 1.0000 - dense_1_acc_10: 1.0000 - dense_1_acc_11: 1.0000 - dense_1_acc_12: 1.0000 - dense_1_acc_13: 1.0000 - dense_1_acc_14: 1.0000 - dense_1_acc_15: 1.0000 - dense_1_acc_16: 1.0000 - dense_1_acc_17: 1.0000 - dense_1_acc_18: 1.0000 - dense_1_acc_19: 1.0000 - dense_1_acc_20: 1.0000 - dense_1_acc_21: 1.0000 - dense_1_acc_22: 1.0000 - dense_1_acc_23: 1.0000 - dense_1_acc_24: 1.0000 - dense_1_acc_25: 1.0000 - dense_1_acc_26: 1.0000 - dense_1_acc_27: 1.0000 - dense_1_acc_28: 1.0000 - dense_1_acc_29: 0.0167
Epoch 56/100
60/60 [==============================] - 0s 2ms/step - loss: 9.1120 - dense_1_loss: 0.0000e+00 - dense_1_acc: 0.0667 - dense_1_acc_1: 0.5000 - dense_1_acc

60/60 [==============================] - 0s 2ms/step - loss: 7.0896 - dense_1_loss: 0.0000e+00 - dense_1_acc: 0.1000 - dense_1_acc_1: 0.6000 - dense_1_acc_2: 0.9000 - dense_1_acc_3: 1.0000 - dense_1_acc_4: 0.9833 - dense_1_acc_5: 1.0000 - dense_1_acc_6: 1.0000 - dense_1_acc_7: 1.0000 - dense_1_acc_8: 1.0000 - dense_1_acc_9: 1.0000 - dense_1_acc_10: 1.0000 - dense_1_acc_11: 1.0000 - dense_1_acc_12: 1.0000 - dense_1_acc_13: 1.0000 - dense_1_acc_14: 1.0000 - dense_1_acc_15: 1.0000 - dense_1_acc_16: 1.0000 - dense_1_acc_17: 1.0000 - dense_1_acc_18: 1.0000 - dense_1_acc_19: 1.0000 - dense_1_acc_20: 1.0000 - dense_1_acc_21: 1.0000 - dense_1_acc_22: 1.0000 - dense_1_acc_23: 1.0000 - dense_1_acc_24: 1.0000 - dense_1_acc_25: 1.0000 - dense_1_acc_26: 1.0000 - dense_1_acc_27: 1.0000 - dense_1_acc_28: 1.0000 - dense_1_acc_29: 0.0167
Epoch 74/100
60/60 [==============================] - 0s 2ms/step - loss: 7.0187 - dense_1_loss: 0.0000e+00 - dense_1_acc: 0.1000 - dense_1_acc_1: 0.6000 - dense_1_acc

60/60 [==============================] - 0s 2ms/step - loss: 6.1853 - dense_1_loss: 0.0000e+00 - dense_1_acc: 0.1000 - dense_1_acc_1: 0.6000 - dense_1_acc_2: 0.9167 - dense_1_acc_3: 1.0000 - dense_1_acc_4: 1.0000 - dense_1_acc_5: 1.0000 - dense_1_acc_6: 1.0000 - dense_1_acc_7: 1.0000 - dense_1_acc_8: 1.0000 - dense_1_acc_9: 1.0000 - dense_1_acc_10: 1.0000 - dense_1_acc_11: 1.0000 - dense_1_acc_12: 1.0000 - dense_1_acc_13: 1.0000 - dense_1_acc_14: 1.0000 - dense_1_acc_15: 1.0000 - dense_1_acc_16: 1.0000 - dense_1_acc_17: 1.0000 - dense_1_acc_18: 1.0000 - dense_1_acc_19: 1.0000 - dense_1_acc_20: 1.0000 - dense_1_acc_21: 1.0000 - dense_1_acc_22: 1.0000 - dense_1_acc_23: 1.0000 - dense_1_acc_24: 1.0000 - dense_1_acc_25: 1.0000 - dense_1_acc_26: 1.0000 - dense_1_acc_27: 1.0000 - dense_1_acc_28: 1.0000 - dense_1_acc_29: 0.0167
Epoch 92/100
60/60 [==============================] - 0s 2ms/step - loss: 6.1483 - dense_1_loss: 0.0000e+00 - dense_1_acc: 0.1000 - dense_1_acc_1: 0.6000 - dense_1_acc

In [11]:
def music_inference_model(LSTM_cell, densor, n_values = 78, n_a = 64, Ty = 100):
   
    x0 = Input(shape=(1, n_values))

    a0 = Input(shape=(n_a,), name='a0')
    c0 = Input(shape=(n_a,), name='c0')
    a = a0
    c = c0
    x = x0

   
    outputs = []

    for t in range(Ty):

        
        a, _, c = LSTM_cell(x, initial_state=[a, c])

        out = densor(a)

        outputs.append(out)

        
        x = Lambda(one_hot)(out)

   
    inference_model = Model([x0, a0, c0], outputs)

    

    return inference_model


In [12]:
inference_model = music_inference_model(LSTM_cell, densor, n_values = 78, n_a = 64, Ty = 50)

In [13]:
x_initializer = np.zeros((1, 1, 78))
a_initializer = np.zeros((1, n_a))
c_initializer = np.zeros((1, n_a))

In [14]:
def predict_and_sample(inference_model, x_initializer = x_initializer, a_initializer = a_initializer, 
                       c_initializer = c_initializer):

    
    pred = inference_model.predict([x_initializer, a_initializer, c_initializer])
  
    indices = np.argmax(pred, 2)
  
    results = to_categorical(indices)
  

    return results, indices



In [15]:
results, indices = predict_and_sample(inference_model, x_initializer, a_initializer, c_initializer)
print("np.argmax(results[12]) =", np.argmax(results[12]))
print("np.argmax(results[17]) =", np.argmax(results[17]))
print("list(indices[12:18]) =", list(indices[12:18]))


np.argmax(results[12]) = 2
np.argmax(results[17]) = 57
list(indices[12:18]) = [array([2]), array([57]), array([71]), array([51]), array([2]), array([57])]


In [16]:
out_stream = generate_music(inference_model)


Predicting new values for different set of chords.
Generated 50 sounds using the predicted values for the set of chords ("1") and after pruning
Generated 51 sounds using the predicted values for the set of chords ("2") and after pruning
Generated 51 sounds using the predicted values for the set of chords ("3") and after pruning
Generated 51 sounds using the predicted values for the set of chords ("4") and after pruning
Generated 51 sounds using the predicted values for the set of chords ("5") and after pruning
Your generated music is saved in output/my_music.midi


In [17]:
IPython.display.Audio('./data/my_music.mp3')